<span style="color:red; font-family:Helvetica Neue, Helvetica, Arial, sans-serif; font-size:2em;">An Exception was encountered at '<a href="#papermill-error-cell">In [13]</a>'.</span>

In [1]:
import torch
from transformers import AutoModelForCausalLM, TrainingArguments, BitsAndBytesConfig
from peft import LoraConfig
from transformers import set_seed
from transformers import AutoTokenizer
from peft import prepare_model_for_kbit_training, get_peft_model
from transformers import DataCollatorForLanguageModeling
from transformers import Trainer
import os
from transformers import pipeline, AutoModelForCausalLM, AutoTokenizer
from peft import PeftModelForCausalLM, PeftModel, PeftConfig
import torch
from datasets import DatasetDict, Dataset
from sklearn.model_selection import train_test_split
import pandas as pd
import gc
import json


2024-10-30 22:56:15.542359: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-10-30 22:56:15.659857: E tensorflow/stream_executor/cuda/cuda_blas.cc:2981] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered


2024-10-30 22:56:16.095516: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer.so.7'; dlerror: libnvinfer.so.7: cannot open shared object file: No such file or directory
2024-10-30 22:56:16.095579: W tensorflow/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libnvinfer_plugin.so.7'; dlerror: libnvinfer_plugin.so.7: cannot open shared object file: No such file or directory
2024-10-30 22:56:16.095585: W tensorflow/compiler/tf2tensorrt/utils/py_utils.cc:38] TF-TRT Warning: Cannot dlopen some TensorRT libraries. If you would like to use Nvidia GPU with TensorRT, please make sure the missing libraries mentioned above are installed properly.


In [2]:
seed = 42
set_seed(seed)

In [3]:
bnb_configs = []

for b in [False,True]:
    for e in [False,True]:
        for f in [ "float32","bfloat16"]:
            bnb_configs.append(
                {
                "load_in_4bit":b,
                "bnb_4bit_use_double_quant":e,
                "bnb_4bit_compute_dtype":f 
                }
            )

len(bnb_configs)

8

In [4]:
lora_configs = []

for a in [1024,64,8,1]:
    for b in [1024,64,8,1]:
        for d in [0.1,0]:
            lora_configs.append(
                {
                    "r":a,
                    "lora_alpha":b,
                    "lora_dropout":d,
                }
            )
                            
len(lora_configs)

32

In [5]:
base_configs = []

for c in [0.1,0]:
    for d in [1e-5,1e-4]:
        for f in [False,True]:
                base_configs.append(
                    {
                        "weight_decay":c,
                        "learning_rate":d,
                        "fp16":f,
                    }
                )

len(base_configs)

8

In [6]:
train_configs = []

for a in [True, False]:
    for b in [False,True]:
        if not a and b: continue
        train_configs.append(
            {
                "lora":a,
                "bnb":b
            }
        )

len(train_configs)

3

In [ ]:
def write_json(new_data, filename='data.json'):
    with open(filename,'r+') as file:
        file_data = json.load(file)
        file_data.append(new_data)
        file.seek(0)
        json.dump(file_data, file, indent = 4)

In [8]:
def create_pipeline_and_print(model,tokenizer,p=False,t=""):
    prompt = "Hello"
    gen = pipeline(model=model, tokenizer=tokenizer, task="text-generation", device_map="auto",max_new_tokens=10)
    result = gen(prompt)[0]["generated_text"]
    if p: print(t, ": ",result)
    
    del gen
    gc.collect()
    
    return result


In [9]:
i = 0

def train_model(base_config, lora_config, bnb_config):
    global i
    
    i += 1
    if i < 793: return
    
    model_name = "TinyLlama/TinyLlama_v1.1"
    
    tokenizer = AutoTokenizer.from_pretrained(model_name)
    tokenizer.pad_token = tokenizer.eos_token

    collator = DataCollatorForLanguageModeling(
        tokenizer=tokenizer,
        mlm=False,
    )

    data = Dataset.from_json("banana.json")
    data = data.map(lambda example : tokenizer(example["text"], return_tensors="np"), batched=True)

    if bnb_config:
        bnb = BitsAndBytesConfig(
            load_in_4bit=bnb_config["load_in_4bit"],
            bnb_4bit_use_double_quant=bnb_config["bnb_4bit_use_double_quant"],
            bnb_4bit_quant_type="nf4",
            bnb_4bit_compute_dtype=bnb_config["bnb_4bit_compute_dtype"]
        )
        
        model = AutoModelForCausalLM.from_pretrained(
                    model_name,
                    device_map="auto",
                    revision="main",
                    quantization_config = bnb
                )
    else:
        model = AutoModelForCausalLM.from_pretrained(
                model_name,
                device_map="auto",
                revision="main"
            )
    
    if lora_config:
        lora = LoraConfig(
            r = lora_config["r"],
            lora_alpha = lora_config["lora_alpha"],
            init_lora_weights = True,
            lora_dropout = lora_config["lora_dropout"],
            bias = 'none',
            task_type="CAUSAL_LM"
        )
        
        model = prepare_model_for_kbit_training(model)
        model = get_peft_model(model,lora)
    
    args = TrainingArguments(
        output_dir=".",
        fp16=base_config["fp16"],
        weight_decay=base_config["weight_decay"],
        learning_rate=base_config["learning_rate"],
        label_names=['input_ids'],
        num_train_epochs=100,
        per_device_train_batch_size=1,
        per_device_eval_batch_size=1,
        gradient_accumulation_steps=1,
        no_cuda=False,
        optim="paged_adamw_8bit",
        eval_steps=1000
    )
    
    trainer = Trainer(
        model=model,
        args=args,
        train_dataset=data,
        tokenizer=tokenizer,
        data_collator=collator
    )
    
    trainer.train()
    save_path = "tmp"
    model.save_pretrained(save_path)


    generation = {"args":base_config,"lora":lora_config,"bnb":bnb_config}

    base_model = AutoModelForCausalLM.from_pretrained(model_name, load_in_8bit=False, torch_dtype="bfloat16")
    
    generation["base"] = create_pipeline_and_print(base_model,tokenizer,tokenizer,t="base")
    
    generation["direct"] = create_pipeline_and_print(model,tokenizer,t="direct")
    
    if lora_config:
        merged_model = model.merge_and_unload()

        generation["merged"] = create_pipeline_and_print(merged_model,tokenizer,t="merged")
    
    
    if lora_config:
        loaded_model = PeftModelForCausalLM.from_pretrained(base_model,save_path)
    else:
        loaded_model = AutoModelForCausalLM.from_pretrained(save_path)
    
    generation["loaded"] = create_pipeline_and_print(loaded_model,tokenizer,t="loaded")
    
    if lora_config:
        merged_loaded_model = loaded_model.merge_and_unload()
        generation["merged_loaded"] = create_pipeline_and_print(merged_loaded_model,tokenizer,t="mergedLoaded")
        
        del loaded_model
        del merged_loaded_model
    
    write_json(generation)
    
    del tokenizer
    del collator
    del data
    del args
    del model
    del base_model
    del merged_model
    del generation
    
    gc.collect()

In [10]:
train_model({"weight_decay":0.1,"learning_rate":1e-5,"fp16":False},
            {"r":1024,"lora_alpha":1024,"lora_dropout":0.1},
            {"load_in_4bit":False,"bnb_4bit_use_double_quant":False,"bnb_4bit_compute_dtype":"float32"}
            #False
            )

In [11]:
"""bnb = BitsAndBytesConfig(
load_in_4bit=True,
bnb_4bit_use_double_quant=True,
bnb_4bit_quant_type="nf4",
bnb_4bit_compute_dtype=torch.bfloat16
)

model = AutoModelForCausalLM.from_pretrained(
    model_name,
    device_map="auto",
    revision="main",
    quantization_config = bnb
)


lora = LoraConfig(
    r = 64,
    lora_alpha = 64,
    init_lora_weights = True,
    lora_dropout = 0.1,
    bias = 'none',
    task_type="CAUSAL_LM"
)

model = prepare_model_for_kbit_training(model)
model = get_peft_model(model,lora)
    
args = TrainingArguments(
    output_dir=".",
    fp16=True,
    weight_decay=0.1,
    learning_rate=1e-5,
    label_names=['input_ids'],
    num_train_epochs=100,
    per_device_train_batch_size=1,
    per_device_eval_batch_size=1,
    gradient_accumulation_steps=1,
    no_cuda=False,
    optim="paged_adamw_8bit",
)
    
trainer = Trainer(
    model=model,
    args=args,
    train_dataset=tokenized_ds,
    tokenizer=tokenizer,
    data_collator=collator
)

trainer.train()
save_path = "tmp"
trainer.save_model(save_path)"""

'bnb = BitsAndBytesConfig(\nload_in_4bit=True,\nbnb_4bit_use_double_quant=True,\nbnb_4bit_quant_type="nf4",\nbnb_4bit_compute_dtype=torch.bfloat16\n)\n\nmodel = AutoModelForCausalLM.from_pretrained(\n    model_name,\n    device_map="auto",\n    revision="main",\n    quantization_config = bnb\n)\n\n\nlora = LoraConfig(\n    r = 64,\n    lora_alpha = 64,\n    init_lora_weights = True,\n    lora_dropout = 0.1,\n    bias = \'none\',\n    task_type="CAUSAL_LM"\n)\n\nmodel = prepare_model_for_kbit_training(model)\nmodel = get_peft_model(model,lora)\n    \nargs = TrainingArguments(\n    output_dir=".",\n    fp16=True,\n    weight_decay=0.1,\n    learning_rate=1e-5,\n    label_names=[\'input_ids\'],\n    num_train_epochs=100,\n    per_device_train_batch_size=1,\n    per_device_eval_batch_size=1,\n    gradient_accumulation_steps=1,\n    no_cuda=False,\n    optim="paged_adamw_8bit",\n)\n    \ntrainer = Trainer(\n    model=model,\n    args=args,\n    train_dataset=tokenized_ds,\n    tokenizer=tok

In [12]:
"""create_pipeline_and_print(model)

base_model = AutoModelForCausalLM.from_pretrained(model_name)
create_pipeline_and_print(base_model)

model = model.merge_and_unload()
create_pipeline_and_print(model)
create_pipeline_and_print(base_model)

loaded_model = AutoModelForCausalLM.from_pretrained(save_path)
create_pipeline_and_print(loaded_model)

peft_model = PeftModelForCausalLM.from_pretrained(base_model,save_path)
create_pipeline_and_print(peft_model)

peft_model = peft_model.merge_and_unload()
create_pipeline_and_print(peft_model)"""

'create_pipeline_and_print(model)\n\nbase_model = AutoModelForCausalLM.from_pretrained(model_name)\ncreate_pipeline_and_print(base_model)\n\nmodel = model.merge_and_unload()\ncreate_pipeline_and_print(model)\ncreate_pipeline_and_print(base_model)\n\nloaded_model = AutoModelForCausalLM.from_pretrained(save_path)\ncreate_pipeline_and_print(loaded_model)\n\npeft_model = PeftModelForCausalLM.from_pretrained(base_model,save_path)\ncreate_pipeline_and_print(peft_model)\n\npeft_model = peft_model.merge_and_unload()\ncreate_pipeline_and_print(peft_model)'

<span id="papermill-error-cell" style="color:red; font-family:Helvetica Neue, Helvetica, Arial, sans-serif; font-size:2em;">Execution using papermill encountered an exception here and stopped:</span>

In [13]:
%%time

for train_config in train_configs:
    for base_config in base_configs:
        if train_config["lora"]:
            for lora_config in lora_configs:
                if train_config["bnb"]:
                    for bnb_config in bnb_configs:
                        train_model(base_config, lora_config, bnb_config)
                else:
                    train_model(base_config, lora_config, False)
        else:
            train_model(base_config, False, False)
            

/home/diekhoff/.local/lib/python3.10/site-packages/torch/cuda/__init__.py:654: UserWarning: Can't initialize NVML
  warnings.warn("Can't initialize NVML")


[2024-10-30 22:56:24,254] [INFO] [real_accelerator.py:203:get_accelerator] Setting ds_accelerator to cuda (auto detect)


 [WARNING]  async_io requires the dev libaio .so object and headers but these were not found.
 [WARNING]  async_io: please install the libaio-dev package with apt
 [WARNING]  If libaio is already installed (perhaps from source), try setting the CFLAGS and LDFLAGS environment variables to where it can be found.
 [WARNING]  Please specify the CUTLASS repo directory as environment variable $CUTLASS_PATH


/usr/bin/ld: cannot find -laio: No such file or directory
collect2: error: ld returned 1 exit status


 [WARNING]  sparse_attn requires a torch version >= 1.5 and < 2.0 but detected 2.4
 [WARNING]  using untested triton version (3.0.0), only 1.0.0 is known to be compatible


...

/home/diekhoff/.local/lib/python3.10/site-packages/peft/tuners/lora/bnb.py:336: UserWarning: Merge lora module to 4-bit linear may get different generations due to rounding errors.
  warnings.warn(


Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.


The model 'PeftModelForCausalLM' is not supported for text-generation. Supported models are ['BartForCausalLM', 'BertLMHeadModel', 'BertGenerationDecoder', 'BigBirdForCausalLM', 'BigBirdPegasusForCausalLM', 'BioGptForCausalLM', 'BlenderbotForCausalLM', 'BlenderbotSmallForCausalLM', 'BloomForCausalLM', 'CamembertForCausalLM', 'LlamaForCausalLM', 'CodeGenForCausalLM', 'CohereForCausalLM', 'CpmAntForCausalLM', 'CTRLLMHeadModel', 'Data2VecTextForCausalLM', 'DbrxForCausalLM', 'ElectraForCausalLM', 'ErnieForCausalLM', 'FalconForCausalLM', 'FuyuForCausalLM', 'GemmaForCausalLM', 'Gemma2ForCausalLM', 'GitForCausalLM', 'GPT2LMHeadModel', 'GPT2LMHeadModel', 'GPTBigCodeForCausalLM', 'GPTNeoForCausalLM', 'GPTNeoXForCausalLM', 'GPTNeoXJapaneseForCausalLM', 'GPTJForCausalLM', 'JambaForCausalLM', 'JetMoeForCausalLM', 'LlamaForCausalLM', 'MambaForCausalLM', 'Mamba2ForCausalLM', 'MarianForCausalLM', 'MBartForCausalLM', 'MegaForCausalLM', 'MegatronBertForCausalLM', 'MistralForCausalLM', 'MixtralForCausal

Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.


ValueError: Some modules are dispatched on the CPU or the disk. Make sure you have enough GPU RAM to fit the quantized model. If you want to dispatch the model on the CPU or the disk while keeping these modules in 32-bit, you need to set `load_in_8bit_fp32_cpu_offload=True` and pass a custom `device_map` to `from_pretrained`. Check https://huggingface.co/docs/transformers/main/en/main_classes/quantization#offload-between-cpu-and-gpu for more details. 